In [ ]:
## Reduction to tridiagonal form!
# We can exactly construct a sequence of orthogonal transformations
# to produce a tridiagonal matrix from an arbitrary symmetric matrix.



In [ ]:
## How Householder Matrices can be used to zero out
using LinearAlgebra
using SparseArrays
function housevec(x)
  v = copy(x)
  normx = norm(x)
  s = -sign(x[1])*normx
  v[1] = v[1] -s

  y = v*(v'*x)
  beta = -1/(s*v[1])
  return v,beta,s
end

""" Return the householder matrix to zero out below the ith row and jth column """
function housemat(A,i,j)
  v,beta,s = housevec(A[i:end,j])
  H = Matrix(1.0I,size(A)...)
  H[i:end,i:end] = H[i:end,i:end] - beta*v*v'
  return H,v,beta,s
end

A = randn(5,5)
A = A + A'

H = housemat(A,2,1)[1]
display(H*A*H')



In [ ]:
##
B = H*A*H'
H2 = housemat(B,3,2)[1]
display(H2*B*H2')


In [ ]:
##
Q = H2*H
display(Q*A*Q')



In [ ]:
##
spones(A::SparseMatrixCSC) = begin fill!(A.nzval, one(eltype(A))); A end
using Plots
pyplot()
using Printf
function animate_myhess(A)
  n = size(A,1)
  V = zeros(n,n) # space to store the householder vectors
  for k = 1:n-2
    x = A[k+1:n,k]
    vk = copy(x)
    vk[1] = x[1] + sign(x[1])*norm(x)
    vk = vk/norm(vk)
    V[k+1:n,k] = vk # store V
    A[k+1:n,k:n] -= 2*vk*(vk'*A[k+1:n,k:n])
    A[1:n,k+1:n] -= 2*(A[1:n,k+1:n]*vk)*vk'
    At = A
    At[abs.(At).<1e-12] .= 0
    spy(-spones(dropzeros!(sparse(At))),markersize = 6.0,
      colorbar=false,axis=false,markercolor=:blue)

    title!(@sprintf("Step %i",k))
    gui()
    sleep(1.5)
  end
  return A,V
end
A = randn(37,37)
A = A + A'
animate_myhess(A)



In [ ]:
##

function myhess(A)
  # myhess Implement algorithm 26.1 from Trefethen and Bau
  n = size(A,1)
  V = zeros(n,n) # space to store the householder vectors
  for k = 1:n-2
    x = A[k+1:n,k]
    vk = copy(x)
    vk[1] = x[1] + sign(x[1])*norm(x)
    vk = vk/norm(vk)
    V[k+1:n,k] = vk # store V
    A[k+1:n,k:n] -= 2*vk*(vk'*A[k+1:n,k:n])
    A[1:n,k+1:n] -= 2*(A[1:n,k+1:n]*vk)*vk'
  end
  return A,V
end



In [ ]:
## show that RQ given QR preserves tridiagonal
A = randn(5,5)
A = A + A'
T = myhess(A)[1]
T = map!(x -> abs(x) > 10*eps(1.0) ? x : 0.0, T, T)
Q,R = qr(T)
display(R*Q)
Q
